<h1><center>Riiid! Answer Correctness Prediction. Data Analysis and visualization.</center></h1>

<center><img src="https://www.riiid.co/assets/opengraph.png"></center>




#### In this competition, your challenge is to create algorithms for "Knowledge Tracing," the modeling of student knowledge over time. The goal is to accurately predict how students will perform on future interactions. You will pair your machine learning skills using Riiid’s EdNet data.

#### Let's check our data before we start this competition!

<a id="top"></a>

<div class="list-group" id="list-tab" role="tablist">
<h3 class="list-group-item list-group-item-action active" data-toggle="list" style='background:black; border:0' role="tab" aria-controls="home"><center>Quick navigation</center></h3>

* [1. train.csv](#1)
* [2. questions.csv](#2)
* [3. lectures.csv](#3)
* [4. example_test.csv](#4)
* [5. Modeling](#5)

In [1]:
import numpy as np
import pandas as pd

import plotly.express as px
from plotly.subplots import make_subplots
import plotly.graph_objs as go

from sklearn.metrics import roc_auc_score
from sklearn.model_selection import train_test_split
from lightgbm import LGBMClassifier

import optuna
from optuna.samplers import TPESampler

import riiideducation
from sklearn.feature_selection import RFE
from sklearn.tree import DecisionTreeClassifier

In [2]:
sampler = TPESampler(
    seed=666
)

<a id="1"></a>
<h2 style='background:black; border:0; color:white'><center>1. train.csv<center><h2>

**train.csv**

* **row_id**: (int64) ID code for the row.

* **timestamp**: (int64) the time between this user interaction and the first event from that user.

* **user_id**: (int32) ID code for the user.

* **content_id**: (int16) ID code for the user interaction

* **content_type_id**: (int8) 0 if the event was a question being posed to the user, 1 if the event was the user watching a lecture.

* **task_container_id**: (int16) Id code for the batch of questions or lectures. For example, a user might see three questions in a row before seeing the explanations for any of them. Those three would all share a task_container_id. Monotonically increasing for each user.

* **user_answer**: (int8) the user's answer to the question, if any. Read -1 as null, for lectures.

* **answered_correctly**: (int8) if the user responded correctly. Read -1 as null, for lectures.

* **prior_question_elapsed_time**: (float32) How long it took a user to answer their previous question bundle, ignoring any lectures in between. The value is shared across a single question bundle, and is null for a user's first question bundle or lecture. Note that the time is the total time a user took to solve all the questions in the previous bundle.

* **prior_question_had_explanation**: (bool) Whether or not the user saw an explanation and the correct response(s) after answering the previous question bundle, ignoring any lectures in between. The value is shared across a single question bundle, and is null for a user's first question bundle or lecture. Typically the first several questions a user sees were part of an onboarding diagnostic test where they did not get any feedback.

In [3]:
types = {
        'row_id': 'int64', 
        'timestamp': 'int64', 
        'user_id': 'int32', 
        'content_id': 'int16', 
        'content_type_id': 'int8',
        'task_container_id': 'int16', 
        'user_answer': 'int8', 
        'answered_correctly': 'int8', 
        'prior_question_elapsed_time': 'float32', 
        'prior_question_had_explanation': 'boolean'
}

In [4]:
train_df = pd.read_csv(
    '/kaggle/input/riiid-test-answer-prediction/train.csv', 
    low_memory=False, 
    nrows=10**6, 
    dtype=types
)

train_df.head()

row_id  timestamp  user_id  content_id  content_type_id  task_container_id  \
0       0          0      115        5692                0                  1   
1       1      56943      115        5716                0                  2   
2       2     118363      115         128                0                  0   
3       3     131167      115        7860                0                  3   
4       4     137965      115        7922                0                  4   

   user_answer  answered_correctly  prior_question_elapsed_time  \
0            3                   1                          NaN   
1            2                   1                      37000.0   
2            0                   1                      55000.0   
3            0                   1                      19000.0   
4            1                   1                      11000.0   

   prior_question_had_explanation  
0                            <NA>  
1                           False  
2                           False  
3                           False  
4                           False

In [5]:
print('Part of missing values for every column')
print(train_df.isnull().sum() / len(train_df))

Part of missing values for every column
row_id                            0.000000
timestamp                         0.000000
user_id                           0.000000
content_id                        0.000000
content_type_id                   0.000000
task_container_id                 0.000000
user_answer                       0.000000
answered_correctly                0.000000
prior_question_elapsed_time       0.023723
prior_question_had_explanation    0.003816
dtype: float64


In [6]:
WIDTH = 800

In [7]:
ds = train_df['user_id'].value_counts().reset_index()

ds.columns = [
    'user_id', 
    'count'
]

ds['user_id'] = ds['user_id'].astype(str) + '-'
ds = ds.sort_values(['count']).tail(40)

fig = px.bar(
    ds, 
    x='count', 
    y='user_id', 
    orientation='h', 
    title='Top 40 users by number of actions', 
    width=WIDTH,
    height=900 
)

fig.show()

In [8]:
ds = train_df['user_id'].value_counts().reset_index()

ds.columns = [
    'user_id', 
    'count'
]

ds = ds.sort_values('user_id')

fig = px.line(
    ds, 
    x='user_id', 
    y='count', 
    title='User action distribution', 
    width=WIDTH,
    height=600 
)

fig.show()

In [9]:
ds = train_df['content_id'].value_counts().reset_index()

ds.columns = [
    'content_id', 
    'count'
]

ds['content_id'] = ds['content_id'].astype(str) + '-'
ds = ds.sort_values(['count']).tail(40)

fig = px.bar(
    ds, 
    x='count', 
    y='content_id', 
    orientation='h', 
    title='Top 40 most useful content_ids',  
    width=WIDTH,
    height=900
)

fig.show()

In [10]:
ds = train_df['content_id'].value_counts().reset_index()

ds.columns = [
    'content_id', 
    'count'
]

ds = ds.sort_values('content_id')

fig = px.line(
    ds, 
    x='content_id', 
    y='count', 
    title='content_id action distribution', 
    width=WIDTH,
    height=600 
)

fig.show()

In [11]:
ds = train_df['content_type_id'].value_counts().reset_index()

ds.columns = [
    'content_type_id', 
    'percent'
]

ds['percent'] /= len(train_df)

fig = px.pie(
    ds, 
    names='content_type_id', 
    values='percent', 
    title='Lecures & questions', 
    width=WIDTH,
    height=500 
)

fig.show()

In [12]:
ds = train_df['task_container_id'].value_counts().reset_index()

ds.columns = [
    'task_container_id', 
    'count'
]

ds['task_container_id'] = ds['task_container_id'].astype(str) + '-'
ds = ds.sort_values(['count']).tail(40)

fig = px.bar(
    ds, 
    x='count', 
    y='task_container_id', 
    orientation='h', 
    title='Top 40 most useful task_container_ids', 
    width=WIDTH,
    height=900
)

fig.show()

In [13]:
ds = train_df['task_container_id'].value_counts().reset_index()

ds.columns = [
    'task_container_id', 
    'count'
]

ds = ds.sort_values('task_container_id')

fig = px.line(
    ds, 
    x='task_container_id', 
    y='count', 
    title='task_container_id action distribution', 
    width=WIDTH,
    height=600  
)

fig.show()

In [14]:
ds = train_df['user_answer'].value_counts().reset_index()

ds.columns = [
    'user_answer', 
    'percent_of_answers'
]

ds['percent_of_answers'] /= len(train_df)
ds = ds.sort_values(['percent_of_answers'])

fig = px.bar(
    ds, 
    x='user_answer', 
    y='percent_of_answers', 
    orientation='v', 
    title='Percent of user answers for every option', 
    width=WIDTH,
    height=400 
)

fig.show()

In [15]:
ds = train_df['answered_correctly'].value_counts().reset_index()

ds.columns = [
    'answered_correctly', 
    'percent_of_answers'
]

ds['percent_of_answers'] /= len(train_df)
ds = ds.sort_values(['percent_of_answers'])

fig = px.pie(
    ds, 
    names='answered_correctly', 
    values='percent_of_answers', 
    title='Percent of correct answers', 
    width=WIDTH,
    height=500 
)

fig.show()

In [16]:
fig = make_subplots(rows=3, cols=2)

traces = [
    go.Bar(
        x=[
            -1, 0, 1
        ], 
        y=[
            len(train_df[(train_df['user_answer'] == item) & (train_df['answered_correctly'] == -1)]),
            len(train_df[(train_df['user_answer'] == item) & (train_df['answered_correctly'] == 0)]),
            len(train_df[(train_df['user_answer'] == item) & (train_df['answered_correctly'] == 1)])
        ], 
        name='Option: ' + str(item),
        text = [
            str(round(100 * len(train_df[(train_df['user_answer'] == item) & (train_df['answered_correctly'] == -1)]) / len(train_df[(train_df['user_answer'] == item)]), 2)) + '%',
            str(round(100 * len(train_df[(train_df['user_answer'] == item) & (train_df['answered_correctly'] == -0)]) / len(train_df[(train_df['user_answer'] == item)]), 2)) + '%',
            str(round(100 * len(train_df[(train_df['user_answer'] == item) & (train_df['answered_correctly'] == 1)]) / len(train_df[(train_df['user_answer'] == item)]), 2)) + '%',
        ],
        textposition='auto'
    ) for item in train_df['user_answer'].unique().tolist()
]

for i in range(len(traces)):
    fig.append_trace(
        traces[i], 
        (i // 2) + 1, 
        (i % 2)  + 1
    )

fig.update_layout(
    title_text='Percent of correct answers for every option',
    height=900,
    width=WIDTH
)

fig.show()

In [17]:
fig = px.histogram(
    train_df, 
    x="prior_question_elapsed_time",
    nbins=50,
    title='prior_question_elapsed_time distribution',
    width=WIDTH,
    height=500
)

fig.show()

<a id="2"></a>
<h2 style='background:black; border:0; color:white'><center>2. questions.csv<center><h2>

**questions.csv**: metadata for the questions posed to users.

* **question_id**: foreign key for the train/test content_id column, when the content type is question (0).

* **bundle_id**: code for which questions are served together.

* **correct_answer**: the answer to the question. Can be compared with the train user_answer column to check if the user was right.

* **part**: top level category code for the question.

* **tags**: one or more detailed tag codes for the question. The meaning of the tags will not be provided, but these codes are sufficient for clustering the questions together.

In [18]:
questions = pd.read_csv('/kaggle/input/riiid-test-answer-prediction/questions.csv')
questions.head()

question_id  bundle_id  correct_answer  part            tags
0            0          0               0     1   51 131 162 38
1            1          1               1     1       131 36 81
2            2          2               0     1  131 101 162 92
3            3          3               0     1  131 149 162 29
4            4          4               3     1    131 5 162 38

In [19]:
print('Part of missing values for every column')
print(questions.isnull().sum() / len(questions))

Part of missing values for every column
question_id       0.000000
bundle_id         0.000000
correct_answer    0.000000
part              0.000000
tags              0.000074
dtype: float64


In [20]:
questions['tag'] = questions['tags'].str.split(' ')
questions = questions.explode('tag')
questions = pd.merge(
    questions, 
    questions.groupby('question_id')['tag'].count().reset_index(), 
    on='question_id'
)

questions = questions.drop(['tag_x'], axis=1)

questions.columns = [
    'question_id', 
    'bundle_id', 
    'correct_answer', 
    'part', 
    'tags', 
    'tags_number'
]

questions = questions.drop_duplicates()

In [21]:
ds = questions['correct_answer'].value_counts().reset_index()

ds.columns = [
    'correct_answer', 
    'number_of_answers'
]

ds['correct_answer'] = ds['correct_answer'].astype(str) + '-'
ds = ds.sort_values(['number_of_answers'])

fig = px.bar(
    ds, 
    x='number_of_answers', 
    y='correct_answer', 
    orientation='h', 
    title='Number of correct answers per group', 
    width=WIDTH,
    height=300
)

fig.show()

In [22]:
ds = questions['part'].value_counts().reset_index()

ds.columns = [
    'part', 
    'count'
]

ds['part'] = ds['part'].astype(str) + '-'
ds = ds.sort_values(['count'])

fig = px.bar(
    ds, 
    x='count', 
    y='part', 
    orientation='h', 
    title='Parts distribution',
    width=WIDTH,
    height=400
)

fig.show()

In [23]:
ds = questions['tags_number'].value_counts().reset_index()

ds.columns = [
    'tags_number', 
    'count'
]

ds['tags_number'] = ds['tags_number'].astype(str) + '-'
ds = ds.sort_values(['tags_number'])

fig = px.bar(
    ds, 
    x='count', 
    y='tags_number', 
    orientation='h', 
    title='Number tags distribution', 
    width=WIDTH,
    height=400 
)

fig.show()

In [24]:
check = questions['tags'].str.split(' ').explode('tags').reset_index()
check = check['tags'].value_counts().reset_index()

check.columns = [
    'tag', 
    'count'
]

check['tag'] = check['tag'].astype(str) + '-'
check = check.sort_values(['count']).tail(40)

fig = px.bar(
    check, 
    x='count', 
    y='tag', 
    orientation='h', 
    title='Top 40 most useful tags', 
    width=WIDTH,
    height=900 
)

fig.show()

<a id="3"></a>
<h2 style='background:black; border:0; color:white'><center>3. lectures.csv<center><h2>

**lectures.csv**: metadata for the lectures watched by users as they progress in their education.

* **lecture_id**: foreign key for the train/test content_id column, when the content type is lecture (1).

* **part**: top level category code for the lecture.

* **tag**: one tag codes for the lecture. The meaning of the tags will not be provided, but these codes are sufficient for clustering the lectures together.

* **type_of**: brief description of the core purpose of the lecture

In [25]:
lectures = pd.read_csv('/kaggle/input/riiid-test-answer-prediction/lectures.csv')
lectures.head()

lecture_id  tag  part           type_of
0          89  159     5           concept
1         100   70     1           concept
2         185   45     6           concept
3         192   79     5  solving question
4         317  156     5  solving question

In [26]:
print('Part of missing values for every column')
print(lectures.isnull().sum() / len(lectures))

Part of missing values for every column
lecture_id    0.0
tag           0.0
part          0.0
type_of       0.0
dtype: float64


In [27]:
ds = lectures['tag'].value_counts().reset_index()

ds.columns = [
    'tag', 
    'count'
]

ds['tag'] = ds['tag'].astype(str) + '-'
ds = ds.sort_values(['count']).tail(40)

fig = px.bar(
    ds, 
    x='count', 
    y='tag', 
    orientation='h', 
    title='Top 40 lectures by number of tags', 
    height=900, 
    width=WIDTH
)

fig.show()

In [28]:
ds = lectures['part'].value_counts().reset_index()

ds.columns = [
    'part', 
    'count'
]

ds['part'] = ds['part'].astype(str) + '-'
ds = ds.sort_values(['count'])

fig = px.bar(
    ds, 
    x='count', 
    y='part', 
    orientation='h', 
    title='Parts distribution', 
    height=400, 
    width=WIDTH
)

fig.show()

In [29]:
ds = lectures['type_of'].value_counts().reset_index()

ds.columns = [
    'type_of', 
    'count'
]

ds = ds.sort_values(['count'])

fig = px.bar(
    ds, 
    x='count', 
    y='type_of', 
    orientation='h', 
    title='type_of column distribution', 
    height=300, 
    width=WIDTH
)

fig.show()

<a id="4"></a>
<h2 style='background:black; border:0; color:white'><center>4. example_test.csv<center><h2>

**example_test.csv** Three sample groups of the test set data as it will be delivered by the time-series API. The format is largely the same as train.csv. There are two different rows that mirror what information the AI tutor actually has available at any given time, but with the user interactions grouped together for the sake of API performance rather than strictly showing information for a single user at a time. Some questions will appear in the hidden test set that have NOT been presented in the train set, emulating the challenge of quickly adapting to modeling newly introduced questions. Their metadata is still in question.csv as usual.

prior_group_responses (string) provides all of the user_answer entries for previous group in a string representation of a list in the first row of the group. All other rows in each group are null. If you are using Python, you will likely want to call eval on the non-null rows. Some rows may be null, or empty lists.

prior_group_answers_correct (string) provides all the answered_correctly field for previous group, with the same format and caveats as prior_group_responses. Some rows may be null, or empty lists.

In [30]:
test_ex = pd.read_csv('/kaggle/input/riiid-test-answer-prediction/example_test.csv')
test_ex

row_id  group_num    timestamp     user_id  content_id  content_type_id  \
0         0          0            0   275030867        5729                0   
1         1          0  13309898705   554169193       12010                0   
2         2          0   4213672059  1720860329         457                0   
3         3          0  62798072960   288641214       13262                0   
4         4          0  10585422061  1728340777        6119                0   
..      ...        ...          ...         ...         ...              ...   
99      104          3  13167339284  1900527744        3004                0   
100     105          3  13167339284  1900527744        3003                0   
101     106          3  64497673060     7792299        7908                0   
102     107          3  62798166743   288641214        9077                0   
103     108          3   2059176357  2018567473       12119                0   

     task_container_id  prior_question_elapsed_time  \
0                    0                          NaN   
1                 4427                      19000.0   
2                  240                      17000.0   
3                  266                      23000.0   
4                  162                      72400.0   
..                 ...                          ...   
99                1179                      24667.0   
100               1179                      24667.0   
101                676                      19000.0   
102                269                      25000.0   
103                591                      20000.0   

    prior_question_had_explanation prior_group_answers_correct  \
0                              NaN                          []   
1                             True                         NaN   
2                             True                         NaN   
3                             True                         NaN   
4                             True                         NaN   
..                             ...                         ...   
99                            True                         NaN   
100                           True                         NaN   
101                           True                         NaN   
102                           True                         NaN   
103                           True                         NaN   

    prior_group_responses  
0                      []  
1                     NaN  
2                     NaN  
3                     NaN  
4                     NaN  
..                    ...  
99                    NaN  
100                   NaN  
101                   NaN  
102                   NaN  
103                   NaN  

[104 rows x 11 columns]

<a id="5"></a>
<h2 style='background:black; border:0; color:white'><center>5. Modeling<center><h2>

In [31]:
used_data_types_dict = {
    'timestamp': 'int64',
    'user_id': 'int32',
    'content_id': 'int16',
    'answered_correctly': 'int8',
    'prior_question_elapsed_time': 'float16',
    'prior_question_had_explanation': 'boolean'
}

In [32]:
train_df = pd.read_csv(
    '/kaggle/input/riiid-test-answer-prediction/train.csv',
    usecols = used_data_types_dict.keys(),
    dtype=used_data_types_dict, 
    index_col = 0
)

/opt/conda/lib/python3.7/site-packages/numpy/lib/arraysetops.py:569: FutureWarning:

elementwise comparison failed; returning scalar instead, but in the future will perform elementwise comparison



In [33]:
features_df = train_df.iloc[:int(9/10 * len(train_df))]
train_df = train_df.iloc[int(9/10 * len(train_df)):]

In [34]:
train_questions_only_df = features_df[features_df['answered_correctly']!=-1]
grouped_by_user_df = train_questions_only_df.groupby('user_id')

user_answers_df = grouped_by_user_df.agg(
    {
        'answered_correctly': [
            'mean', 
            'count', 
            'std', 
            'median', 
            'skew'
        ]
    }
).copy()

user_answers_df.columns = [
    'mean_user_accuracy', 
    'questions_answered', 
    'std_user_accuracy', 
    'median_user_accuracy', 
    'skew_user_accuracy'
]

user_answers_df

mean_user_accuracy  questions_answered  std_user_accuracy  \
user_id                                                                 
115                   0.695652                  46           0.465215   
124                   0.233333                  30           0.430183   
2746                  0.578947                  19           0.507257   
5382                  0.672000                 125           0.471374   
8623                  0.642202                 109           0.481566   
...                        ...                 ...                ...   
1933700710            0.624829                1466           0.484332   
1933703805            0.650000                  40           0.483046   
1933711038            0.684211                  38           0.471069   
1933715576            0.375000                  16           0.500000   
1933715875            0.779843                5219           0.414392   

            median_user_accuracy  skew_user_accuracy  
user_id                                               
115                          1.0           -0.879359  
124                          0.0            1.328338  
2746                         1.0           -0.347892  
5382                         1.0           -0.741648  
8623                         1.0           -0.601619  
...                          ...                 ...  
1933700710                   1.0           -0.516175  
1933703805                   1.0           -0.653746  
1933711038                   1.0           -0.825545  
1933715576                   0.0            0.571429  
1933715875                   1.0           -1.351136  

[354308 rows x 5 columns]

In [35]:
grouped_by_content_df = train_questions_only_df.groupby('content_id')
content_answers_df = grouped_by_content_df.agg(
    {
        'answered_correctly': [
            'mean', 
            'count', 
            'std', 
            'median', 
            'skew'
        ]
    }
).copy()

content_answers_df.columns = [
    'mean_accuracy', 
    'question_asked', 
    'std_accuracy', 
    'median_accuracy', 
    'skew_accuracy'
]

content_answers_df

mean_accuracy  question_asked  std_accuracy  median_accuracy  \
content_id                                                                 
0                0.908595            6236      0.288207              1.0   
1                0.891682            6684      0.310805              1.0   
2                0.554656           40499      0.497010              1.0   
3                0.779348           20734      0.414696              1.0   
4                0.613226           28549      0.487020              1.0   
...                   ...             ...           ...              ...   
13518            0.789203             778      0.408137              1.0   
13519            0.567797             826      0.495682              1.0   
13520            0.678524             759      0.467351              1.0   
13521            0.822560             789      0.382283              1.0   
13522            0.914174             769      0.280289              1.0   

            skew_accuracy  
content_id                 
0               -2.836339  
1               -2.521185  
2               -0.219949  
3               -1.347371  
4               -0.465009  
...                   ...  
13518           -1.420839  
13519           -0.274213  
13520           -0.766003  
13521           -1.691836  
13522           -2.963045  

[13519 rows x 5 columns]

In [36]:
del features_df
del grouped_by_user_df
del grouped_by_content_df

In [37]:
features = [
    'mean_user_accuracy', 
    'questions_answered',
    'std_user_accuracy', 
    'median_user_accuracy',
    'skew_user_accuracy',
    'mean_accuracy', 
    'question_asked',
    'std_accuracy', 
    'median_accuracy',
    'prior_question_elapsed_time', 
    'prior_question_had_explanation',
    'skew_accuracy'
]

target = 'answered_correctly'

In [38]:
train_df = train_df[train_df[target] != -1]

In [39]:
train_df = train_df.merge(user_answers_df, how='left', on='user_id')
train_df = train_df.merge(content_answers_df, how='left', on='content_id')

In [40]:
train_df['prior_question_had_explanation'] = train_df['prior_question_had_explanation'].fillna(value=False).astype(bool)
train_df = train_df.fillna(value=0.5)

In [41]:
train_df = train_df[features + [target]]
train_df = train_df.replace([np.inf, -np.inf], np.nan)
train_df = train_df.fillna(0.5)

train_df

mean_user_accuracy  questions_answered  std_user_accuracy  \
0                  0.779843              5219.0           0.414392   
1                  0.779843              5219.0           0.414392   
2                  0.779843              5219.0           0.414392   
3                  0.779843              5219.0           0.414392   
4                  0.779843              5219.0           0.414392   
...                     ...                 ...                ...   
9926946            0.500000                 0.5           0.500000   
9926947            0.500000                 0.5           0.500000   
9926948            0.500000                 0.5           0.500000   
9926949            0.500000                 0.5           0.500000   
9926950            0.500000                 0.5           0.500000   

         median_user_accuracy  skew_user_accuracy  mean_accuracy  \
0                         1.0           -1.351136       0.532146   
1                         1.0           -1.351136       0.584772   
2                         1.0           -1.351136       0.603571   
3                         1.0           -1.351136       0.694888   
4                         1.0           -1.351136       0.765869   
...                       ...                 ...            ...   
9926946                   0.5            0.500000       0.738732   
9926947                   0.5            0.500000       0.524581   
9926948                   0.5            0.500000       0.616455   
9926949                   0.5            0.500000       0.660559   
9926950                   0.5            0.500000       0.657680   

         question_asked  std_accuracy  median_accuracy  \
0                1291.0      0.499159              1.0   
1                2548.0      0.492858              1.0   
2                1960.0      0.489280              1.0   
3                2504.0      0.460547              1.0   
4                1922.0      0.423565              1.0   
...                 ...           ...              ...   
9926946          3927.0      0.439382              1.0   
9926947          9194.0      0.499423              1.0   
9926948         28174.0      0.486258              1.0   
9926949          5185.0      0.473565              1.0   
9926950          5638.0      0.474528              1.0   

         prior_question_elapsed_time  prior_question_had_explanation  \
0                            13000.0                            True   
1                            44000.0                            True   
2                            22000.0                            True   
3                                0.5                            True   
4                             9000.0                            True   
...                              ...                             ...   
9926946                      18000.0                            True   
9926947                      14000.0                            True   
9926948                      14000.0                            True   
9926949                      22000.0                            True   
9926950                      28992.0                            True   

         skew_accuracy  answered_correctly  
0            -0.128999                   0  
1            -0.344273                   1  
2            -0.423795                   1  
3            -0.847011                   1  
4            -1.256695                   1  
...                ...                 ...  
9926946      -1.087226                   1  
9926947      -0.098460                   1  
9926948      -0.479018                   1  
9926949      -0.678349                   0  
9926950      -0.664812                   1  

[9926951 rows x 13 columns]

In [42]:
train_df, test_df = train_test_split(train_df, random_state=666, test_size=0.2)

In [43]:
rfe = RFE(
    estimator=DecisionTreeClassifier(
        random_state=666
    ), 
    n_features_to_select=8
)

In [44]:
rfe.fit(train_df[features], train_df[target])
X_transformed = rfe.transform(train_df[features])
X_transformed = pd.DataFrame(X_transformed)

In [45]:
X_transformed.columns = ['col_1', 'col_2', 'col_3', 'col_4', 'col_5', 'col_6', 'col_7', 'col_8']
X_transformed

col_1     col_2  col_3     col_4 col_5  col_6  col_7      col_8
0         0.5  0.751375  28179  0.432224     1  19008   True   -1.16325
1         0.5  0.362581   5687  0.480788     0  25744   True   0.571841
2         0.5  0.492388  58326  0.499946     0  46016   True  0.0304539
3         0.5  0.691253   9626  0.462001     1  44000   True  -0.828105
4         0.5  0.661801  14728  0.473113     1  26000   True  -0.684076
...       ...       ...    ...       ...   ...    ...    ...        ...
7941555   0.5  0.918073  12743  0.274265     1  38016  False   -3.04916
7941556   0.5   0.78625   6400  0.409984     1  19008   True   -1.39683
7941557   0.5  0.756741  17282  0.429063     1  33664   True   -1.19689
7941558   0.5  0.585841   4619   0.49263     1  63008   True  -0.348653
7941559   0.5  0.547862   6456  0.497742     1  63008   True  -0.192378

[7941560 rows x 8 columns]

In [46]:
X_transformed_test = rfe.transform(test_df[features])
X_transformed_test = pd.DataFrame(X_transformed_test)

In [47]:
X_transformed_test.columns = ['col_1', 'col_2', 'col_3', 'col_4', 'col_5', 'col_6', 'col_7', 'col_8']
X_transformed_test

col_1     col_2  col_3     col_4 col_5  col_6  col_7     col_8
0         0.5  0.969813   5201  0.171117     1  22000   True  -5.49326
1         0.5  0.969011   4905  0.173305     1  22672   True  -5.41476
2         0.5  0.699637  15984   0.45843     1  16992  False -0.871069
3         0.5  0.805476   6282  0.395865     1  47008   True  -1.54382
4         0.5  0.844736   3201  0.362213     1   1000   True  -1.90469
...       ...       ...    ...       ...   ...    ...    ...       ...
1985386   0.5  0.612583  39944  0.487166     1  18000   True -0.462217
1985387   0.5  0.669673   1774  0.470463     1  28000   True -0.722116
1985388   0.5  0.642119   5323  0.479422     1  48800   True   -0.5931
1985389   0.5  0.832413   3986  0.373546     1  14000   True  -1.78067
1985390   0.5   0.57886  15629  0.493758     1  13000   True -0.319468

[1985391 rows x 8 columns]

In [48]:
X_transformed_test['col_1'] = X_transformed_test['col_1'].astype(np.float32)
X_transformed_test['col_2'] = X_transformed_test['col_2'].astype(np.float32)
X_transformed_test['col_3'] = X_transformed_test['col_3'].astype(np.int32)
X_transformed_test['col_4'] = X_transformed_test['col_4'].astype(np.float32)
X_transformed_test['col_5'] = X_transformed_test['col_5'].astype(np.int32)
X_transformed_test['col_6'] = X_transformed_test['col_6'].astype(np.int32)
X_transformed_test['col_7'] = X_transformed_test['col_7'].astype(np.int32)
X_transformed_test['col_8'] = X_transformed_test['col_8'].astype(np.float32)

X_transformed['col_1'] = X_transformed['col_1'].astype(np.float32)
X_transformed['col_2'] = X_transformed['col_2'].astype(np.float32)
X_transformed['col_3'] = X_transformed['col_3'].astype(np.int32)
X_transformed['col_4'] = X_transformed['col_4'].astype(np.float32)
X_transformed['col_5'] = X_transformed['col_5'].astype(np.int32)
X_transformed['col_6'] = X_transformed['col_6'].astype(np.int32)
X_transformed['col_7'] = X_transformed['col_7'].astype(np.int32)
X_transformed['col_8'] = X_transformed['col_8'].astype(np.float32)

In [49]:
 def create_model(trial):
    num_leaves = trial.suggest_int("num_leaves", 2, 31)
    n_estimators = trial.suggest_int("n_estimators", 50, 300)
    max_depth = trial.suggest_int('max_depth', 3, 8)
    min_child_samples = trial.suggest_int('min_child_samples', 100, 1200)
    learning_rate = trial.suggest_uniform('learning_rate', 0.0001, 0.99)
    min_data_in_leaf = trial.suggest_int('min_data_in_leaf', 5, 90)
    bagging_fraction = trial.suggest_uniform('bagging_fraction', 0.0001, 1.0)
    feature_fraction = trial.suggest_uniform('feature_fraction', 0.0001, 1.0)
    
    model = LGBMClassifier(
        num_leaves=num_leaves,
        n_estimators=n_estimators, 
        max_depth=max_depth, 
        min_child_samples=min_child_samples, 
        min_data_in_leaf=min_data_in_leaf,
        learning_rate=learning_rate,
        feature_fraction=feature_fraction,
        random_state=666
    )
    return model

def objective(trial):
    model = create_model(trial)
    model.fit(X_transformed, train_df[target])
    score = roc_auc_score(
        test_df[target].values, 
        model.predict_proba(X_transformed_test)[:,1]
    )
    return score

# uncomment to use optuna
# final params is in study.best_params
# study = optuna.create_study(direction="maximize", sampler=sampler)
# study.optimize(objective, n_trials=70)
# params = study.best_params
# params['random_state'] = 666



params = {
    'bagging_fraction': 0.5817242323514327,
    'feature_fraction': 0.6884588361650144,
    'learning_rate': 0.42887924851375825, 
    'max_depth': 6,
    'min_child_samples': 946, 
    'min_data_in_leaf': 47, 
    'n_estimators': 169,
    'num_leaves': 29,
    'random_state': 666
}

model = LGBMClassifier(
    **params
)

model.fit(X_transformed, train_df[target])
print('LGB score: ', roc_auc_score(test_df[target].values, model.predict_proba(X_transformed_test)[:,1]))

LGB score:  0.7216972388150767


In [50]:
env = riiideducation.make_env()
iter_test = env.iter_test()

In [51]:
for (test_df, sample_prediction_df) in iter_test:
    test_df = test_df.merge(user_answers_df, how='left', on='user_id')
    test_df = test_df.merge(content_answers_df, how='left', on='content_id')
    test_df['prior_question_had_explanation'] = test_df['prior_question_had_explanation'].fillna(value=False).astype(bool)
    test_df.fillna(value = 0.5, inplace = True)
    
    test = rfe.transform(test_df)
    test = pd.DataFrame(test)
    test['col_1'] = test['col_1'].astype(np.float32)
    test['col_2'] = test['col_2'].astype(np.float32)
    test['col_3'] = test['col_3'].astype(np.int32)
    test['col_4'] = test['col_4'].astype(np.float32)
    test['col_5'] = test['col_5'].astype(np.int32)
    test['col_6'] = test['col_6'].astype(np.int32)
    test['col_7'] = test['col_7'].astype(np.int32)
    test['col_8'] = test['col_8'].astype(np.float32)


    test_df['answered_correctly'] = model.predict_proba(test)[:,1]
    env.predict(test_df.loc[test_df['content_type_id'] == 0, ['row_id', 'answered_correctly']])

ValueError: X has a different shape than during fitting.